In [ ]:
import numpy as np
import pandas as pd

pd.options.plotting.backend = "plotly"

from gettsim import (
    compute_taxes_and_transfers,
    create_synthetic_data,
    set_up_policy_environment,
)

# Präsenzphase: Bürgergeld

In diesem Notebook beschäftigen wir uns mit dem Bürgergeld. 

Analog zu den Steuern schauen wir uns zunächst an, wie sich die Transfers ändern, wenn wir das Bruttoeinkommen
ändern. Zum einen die gesamten Transfers, zum anderen die Transferentzugsrate, die analog zum Grenzsteuersatz
definiert ist. 

Dieser Teil ist vorprogrammiert. Bitte gehen Sie wie üblich langsam durch und versuchen Sie, die einzelnen
Schritte zu verstehen.

Anschließend bringen wir Transfers und Steuern zusammen, und Sie berechnen selbständig die Gesamtbelastung.

## Datensatzerstellung (5 Minuten)

Wir betrachten heute Haushalte mit einem Erwachsenen, zwei Erwachsenen mit gleichem Einkommen und zwei Erwachsenen mit nur einem Einkommen. Das gesamte Haushaltseinkommen ist über die drei Haushaltstypen hinweg gleich.

In [ ]:
min_einkommen = 0
max_einkommen = 3000
anzahl_schritte = 301

_bruttlohn_m = np.linspace(min_einkommen, max_einkommen, anzahl_schritte)

In [ ]:
df_1e = create_synthetic_data(
    n_adults=1,
    n_children=0,
    specs_heterogeneous={
        "bruttolohn_m": [[i] for i in _bruttlohn_m],
    },
)

df_1e

In [ ]:
df_2e_gleiche_ek = create_synthetic_data(
    n_adults=2,
    n_children=0,
    specs_heterogeneous={
        "bruttolohn_m": [[i, i] for i in _bruttlohn_m / 2],
    },
)

df_2e_gleiche_ek

In [ ]:
df_2e_ein_ek = create_synthetic_data(
    n_adults=2,
    n_children=0,
    specs_heterogeneous={
        "bruttolohn_m": [[i, 0] for i in _bruttlohn_m],
    },
)

df_2e_ein_ek

Wir benötigen eindeutige Haushalts- und Steuereinheits-IDs. (Die Personen-IDs werden später angepasst.)

In [ ]:
# Der Operator += addiert dem Wert linkerhand den Wert rechterhand hinzu.
for c in "hh_id", "tu_id":
    df_2e_gleiche_ek[c] += 1 + df_1e[c].max()

for c in "hh_id", "tu_id":
    df_2e_ein_ek[c] += 1 + df_2e_gleiche_ek[c].max()

## Gruppieren der Datensätze (2 Minuten)

Alle Datensätze haben die gleiche Struktur. Wir können sie wieder direkt aneinander hängen. Im Index können wir über den key "Haushaltstyp" identifizieren, aus welchem ursprünglichen Datensatz die Zeile stammt.

In [ ]:
inputs = pd.concat(
    [
        df_1e,
        df_2e_gleiche_ek,
        df_2e_ein_ek,
    ],
    keys=[
        "1 Erwachsener",
        "2 Erwachsene, gleiche Einkommen",
        "2 Erwachsene, 1 Einkommen",
    ],
    names=["Haushaltstyp", "lfd_nr"],
)
# Jetzt erstellen wir noch eine eindeutige Personen-ID.
inputs["p_id"] = range(len(inputs))
inputs

Ein paar Inputs müssen wir noch von Hand bestimmen/überschreiben. Wir nehmen auch an, dass Miete und Heizkosten für alle Haushalte identisch sind, damit diese Variablen unsere Ergebnisse nicht verzerren.

In [ ]:
inputs["_zu_verst_eink_ohne_kinderfreib_tu"] = (
    inputs.groupby("tu_id")["bruttolohn_m"].transform("sum") * 12
)
inputs["heizkosten_m_hh"] = 50.0
inputs["bruttokaltmiete_m_hh"] = 350.0

## Anwendung von GETTSIM für Bürgergeld und Steuern (5 Minuten)

Wir setzen wieder die Parameter des Steuer- und Transfersystems auf die des Jahres 2023 fest.

In [ ]:
params_dict, policy_func_dict = set_up_policy_environment("2023-01-01")

Außerdem bestimmen wir wieder die Targets (Einkommensteuer, Solidaritätszuschlag,
Sozialversicherungsbeiträge und das Bürgergeld) sowie die Spalten, die überschrieben
werden sollen. Das target für das Bürgergeld ist `arbeitsl_geld_2_vor_vorrang_m_hh`.
Normalerweise wäre die Zielvariable `arbeitsl_geld_2_m_hh` — die Version "vor_vorrang"
berücksichtigt noch nicht, ob andere soziale Zahlungen Vorrang vor dem Bürgergeld hätten
und dadurch kein oder weniger Bürgergeld gezahlt würde. Das interessiert uns heute
nicht.

In [ ]:
targets = [
    "eink_st_tu",
    "soli_st_tu",
    "sozialv_beitr_m",
    "arbeitsl_geld_2_vor_vorrang_m_hh",
]

columns_overriding_functions = [
    "_zu_verst_eink_ohne_kinderfreib_tu",
]

Nun rufen wir GETTSIM auf.

Funktionen und Parameter übernehmen wir direkt aus dem Steuersystem: `policy_func_dict` und `params_dict`.

In [ ]:
ergebnisse_personen = compute_taxes_and_transfers(
    data=inputs,
    functions=policy_func_dict,
    columns_overriding_functions=columns_overriding_functions,
    params=params_dict,
    targets=targets,
    rounding=False,
)
ergebnisse_personen

## Daten auf Haushaltsebene (5 Minuten)

In [ ]:
# Mithilfe der p_id wieder hh_id, bruttolohn_m und Haushaltstyp an das DataFrame joinen.
gesamt_personen = ergebnisse_personen.join(
    inputs.reset_index().set_index("p_id")[["hh_id", "bruttolohn_m", "Haushaltstyp"]],
)
gesamt_personen

In [ ]:
# Zahlen auf Haushaltsebene aggregieren.
ergebnisse = gesamt_personen.groupby("hh_id").agg(
    {
        "bruttolohn_m": lambda x: x.sum(),
        "Haushaltstyp": lambda x: x.iloc[0],
        "eink_st_tu": lambda x: x.max() / 12,
        "soli_st_tu": lambda x: x.max() / 12,
        "sozialv_beitr_m": lambda x: x.sum(),
        "arbeitsl_geld_2_vor_vorrang_m_hh": lambda x: x.max(),
    },
)
ergebnisse = ergebnisse.set_index("Haushaltstyp")
ergebnisse

## Transfers und Transferentzugsrate (3 Minuten)


In [ ]:
ergebnisse = ergebnisse.rename(
    columns={"arbeitsl_geld_2_vor_vorrang_m_hh": "transfers"},
)

In [ ]:
ergebnisse.reset_index().plot.line(
    x="bruttolohn_m",
    y="transfers",
    color="Haushaltstyp",
    title="Transfers nach Haushalts-Bruttolohn",
)

## Aufgabe 1: Interpretation der Transfers (20 Minuten)

Betrachten Sie nur die Haushalte mit zwei Erwachsenen. Warum sind die Bürgergeldbeträge
in der Regel höher, wenn beide Personen Einkommen erzielen, jedoch nicht im Bereich um
1.000 € des gesamten Bruttolohns?

*Hinweis:* Ein Blick in § 11b SGB II könnte weiterhelfen.

## Aufgabe 2: Interpretation der Transferentzugsrate (15 Minuten)

In [ ]:
ergebnisse["transferentzugsrate"] = (
    ergebnisse["transfers"] - ergebnisse.groupby("Haushaltstyp")["transfers"].shift(-1)
) / 10
ergebnisse

Plotten Sie die Transferentzugsrate nach Haushaltstyp und Bruttolohn.

Erklären Sie die Sprünge in den Linien für die Transferentzugsraten!

## Aufgabe 3: Verfügbares Einkommen und gesamte Grenzbelastung (10 Minuten)

Wiederholen Sie die Analyse ab "Transfers und Transferentzugsrate" für das verfügbare Haushaltseinkommen und die gesamte Grenzbelastung aus Transferentzug und Steuern!


Zunächst berechnen wir das verfügbare Einkommen als Summe aller Einkünfte abzüglich der Steuern und Sozialversicherungsbeiträge.

In [ ]:
ergebnisse["verfügbares_einkommen"] = (
    ergebnisse["bruttolohn_m"]
    + ergebnisse["transfers"]
    - ergebnisse["eink_st_tu"]
    - ergebnisse["soli_st_tu"]
    - ergebnisse["sozialv_beitr_m"]
)

Rechnen Sie bitte die Grenzbelastung aus und plotten anschließend die Ergebnisse (verfügbares Einkommen und Grenzbelastung).

Sie können den code von oben fast 1:1 wiederverwenden, nur bei der Berechnung der gesamten Grenzbelastung müssen Sie ein wenig überlegen / ausprobieren.

In [ ]:
ergebnisse

In [ ]:
ergebnisse.groupby("Haushaltstyp")["verfügbares_einkommen"].shift(-1)

## Aufgabe 4: Arbeitsanreize (10 Minuten)

Diskutieren Sie die Größenordnungen der Steuern und Transfers, das resultierende verfügbare Einkommen und die entsprechenden Arbeitsanreize. Es gibt keine richtigen und falschen Antworten.


## Aufgabe 5: Reform der Hinzuverdienstgrenzen (10 Minuten)

Zum 1.07. 2023 wurden die Freibeträge für Einkommen zwischen 520€ und 1000€ auf 30% angehoben. Für nähere Informationen können Sie diese
[Website](https://www.buerger-geld.org/news/buergergeld-ab-1-7-2023-hinzuverdienstgrenzen-werden-angehoben/#:~:text=Ab%20dem%201.%20Juli%202023%20gelten%20h%C3%B6here%20Grenzen%20f%C3%BCr%20den,es%20bei%20der%20aktuellen%20Regelung.)
aufrufen. Was denken Sie, wie könnte sich die Reform auf die Arbeitsanreize auswirken?
Nutzen Sie zur Beantwortung der Frage einen Graphen Ihrer Wahl (wie oben). *Wenn Sie
möchten können Sie nur Einzelpersonen vergleichen. Sollte Sie dies zu viel Zeit kostet,
lassen Sie es jedoch bitte.*

Um das Bürgergeld entsprechend zu berechnen setzen wir die policy Umgebung auf den 1.7.2023.

In [ ]:
params_dict, policy_func_dict = set_up_policy_environment("2023-07-01")

Bitte nutzen Sie wie oben die `compute_taxes_and_transfers` Funktion.

Wie wirkt sich die Reform möglicherweise auf die Arbeitsanreize aus je nach Einkommen?

## Aufgabe 6: Pentabilities (10 Minuten)

Bitte bewerten Sie die Beiträge zur Gruppenarbeit in der Pentabilities-App. Bitte
vergeben Sie über alle 5 Dimensionen hinweg Punkte für die Verhaltensweisen, welche Sie
heute beobachten konnten. Denken Sie bitte daran, sowohl die Beiträge der
Kommiliton:innen Ihrer Gruppe als auch Ihre eigenen zu bewerten.